# Fundamentals of data and coding for psychology

## Representing decimal numbers, with an application in sounds

The learning objectives for this lesson are for you to be able to:

* Compute with non-integers using the `float` datatype.
* Generate and interrogate sounds using `numpy` arrays of `float`s.
* Compute statistical tests and use simulations to demonstrate their properties.

### Non-integers in Python

So far, we have only been considering representations of integers.
However, it is of course vital that we are able to represent and compute with non-integers such as `0.1`.
In programming languages, such numbers are typically referred to as "floating point numbers" or "floats".

In [ ]:
num = 0.1
print(type(num))

We won't go into details about how floats are represented in their underlying binary (see Python's [Floating Point Arithmetic: Issues and Limitations](https://docs.python.org/3/tutorial/floatingpoint.html) if interested), but the key point to know is that some seemingly innocuous numbers like `0.1` cannot be represented *exactly* due to their binary implementation.

For example, let's look at `num` with an increased number of decimal places:

In [ ]:
print(format(num, ".64f"))

As you can see, at some point it starts to diverge from what we would expect from an exact representation of `0.1`.

It is important to note that **this is not a limitation of Python**&mdash;this is a consequence of the binary foundation of floats and is present in pretty much all programming languages.

Happily, the loss of precision is small enough to be of no consequence for typical usage (and there are ways around it for the unusual situations in which such precision is important).

However, there is a situation in which such imprecision can lead to baffling results: when we naively test for equality of floats.
For example, here we have the seemingly bizarre situation where Python is telling us that $\left(0.1 + 0.1 + 0.1\right) \neq 0.3$:

In [ ]:
num_sum = 0.1 + 0.1 + 0.1

print(num_sum == 0.3)

Why? We can see when we look at the contents of the two variables&mdash;Python is correct, they aren't exactly the same:

In [ ]:
print(format(num_sum, ".64f"))
print(format(0.3, ".64f"))

So how can we 'safely' compare two floats for equality?

The best way is to use functions specifically designed for this purpose that take into account the inexact nature of floats.
For example, the built-in package `math` has an `isclose` function:

In [ ]:
import math

math.isclose?

In [ ]:
print(math.isclose(num_sum, 0.3))

The key point is to be careful when comparing the equality of two floats.
I'd say that pretty much every programmer has been 'bitten' by a bug involving such an erroneous test of equality (I certainly have, and sad to say many times).

### Floats in `numpy`

Arrays of floats are straightforward to use in `numpy`; they are typically the default data type, so we don't need to worry about passing explicit arguments to the  `dtype` parameter like we have been doing:

In [ ]:
import numpy as np

float_array = np.ones(5)
print(float_array)
print(float_array.dtype)

Such arrays are not immune to the inexact representation issue we have just discussed:

In [ ]:
num_array = float_array * 0.1

print((num_array + num_array + num_array) == 0.3)

A comparable function to `math.isclose` for arrays is `np.isclose`:

In [ ]:
print(np.isclose(num_array + num_array + num_array, 0.3))

### Using floats to represent sounds

To apply floats and to practice with arrays and numerical representations, we are now going to play around with some sounds.

Before we do so, however, **please first turn your computer's volume to a very low level**.
You can always turn it up if you can't hear the sounds very well, but you can't undo the potential damage and shock of an unexpectedly loud sound.

Sounds can be represented digitally by a series of *samples* that each indicates the voltage at which some external device (e.g., a loudspeaker) is to be fed at that particular timepoint.
These samples are at quite a rapid rate&mdash;typical sampling rates are 44.1kHz and 48kHz (44100 and 48000 samples per second).
Here, we will assume a sample rate of 48kHz.

In [ ]:
sample_rate = 48000

Here, we will represent each sample as a float in the range of -1.0 to +1.0.

(Note that digital audio is actually represented internally as integers, most commonly with 16-bits per sample but sometimes with 24-bits per sample. But it is common to deal with them using floats, and allow the compute to handle the conversion to integers.)

Let's start by generating a 1000Hz 'pure tone' of 1 second duration.
A pure tone consists only of a sinusoidal oscillation at a particular frequency.

First, let's generate an array to represent time, in seconds.
Because we want our sound to have a duration of 1 second, the size of the array will be 1 multiplied by our sampling rate (because the sampling rate is defined as the number of samples per second):

In [ ]:
n_samples = sample_rate * 1
print(n_samples)

Now we want our time array to range from 0 at the first sample to 1 at the last sample, varying linearly in between those samples.
To generate such an array, we can use the `np.linspace` ('linear spacing') function:

In [ ]:
time_s = np.linspace(start=0, stop=1, num=n_samples)

Let's have a look at it, using the plotting routines that we learned about last week:

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt

plt.plot(time_s);
plt.xlabel("Sample");
plt.ylabel("Time (s)");

OK, so now we know the time that each of our samples relates to.
Our next job is to calculate the sound level at each of those samples.

Our task was to generate a pure tone, so we want the sound level to be a sinusoidal function of time.
One complete cycle of a sinusoid happens between $0$ and $2\pi$, so let's first look at the output of the `np.sin` function if we convert our `t` array from 0 to 1 to $0$ to $2\pi$:

In [ ]:
waveform = np.sin(time_s * 2.0 * np.pi)

In [ ]:
plt.plot(waveform);
plt.xlabel("Sample");
plt.ylabel("Output");

As you can see, that gives us one oscillation within the one second.
To generate our desired waveform, we can multiply the input to `np.sin` by the desired frequency&mdash;here, 1000.

In [ ]:
waveform = np.sin(time_s * 2.0 * np.pi * 1000.0)

In [ ]:
plt.plot(waveform);
plt.xlabel("Sample");
plt.ylabel("Output");

That plot doesn't show us very much, as you can see (well, as you can't see).
There are just too many oscillations to be visible.

Let's instead just look at a shorter time window of 0.01 seconds (10 milliseconds).
If we have done our generation correctly, then we should see 10 oscillations within that window.

In [ ]:
win_samples = int(sample_rate * 0.01)

Note the use of `int` above; that function explicitly converts a `float` to an integer.
Why does that make sense here?

In [ ]:
plt.plot(waveform[:win_samples]);
plt.xlabel("Sample");
plt.ylabel("Output");

OK, we have our waveform! Let's have a listen.

To do so, we can use functionality in the `IPython.display` ('interactive Python') package called `Audio`.
It returns a nifty little 'player' that we can use.

In [ ]:
import IPython.display

In [ ]:
player = IPython.display.Audio(data=waveform, rate=sample_rate)

In [ ]:
player

#### What about stereo?

In the above, we just provided one array&mdash;but most sound systems are *stereo*, in they can play different sounds in two different channels (e.g., to the left and right ears if using headphones).

If we inspect the help of `IPython.display.Audio` (via `IPython.display.Audio?`), we can see that the `data` parameter can be a two-dimensional array, where the first dimension indexes the channel and the second dimension indexes the sample.

Let's say we only want to play our tone to one ear and just have silence in the other.
We can do that by first generating a silence waveform:

In [ ]:
silence = np.zeros(n_samples)

Now we have our two channel arrays, `waveform` and `silence`.
How can we convert those two one-dimensional arrays into a single two-dimensional array?

In this particular situation, we can use the function `np.vstack` to 'vertically stack' our two arrays.
If you think back to our table analogy, that is what we want to do; the columns define time and the rows define channels, so we want to vertically (i.e, row-wise) stack the waveforms.

In [ ]:
stereo_waveform = np.vstack([waveform, silence])
print(stereo_waveform.shape)

In [ ]:
player = IPython.display.Audio(data=stereo_waveform, rate=sample_rate)

In [ ]:
player

You will likely need headphones to check that it is working as expected.

*Exercise*: [Binaural beats](https://en.wikipedia.org/wiki/Beat_%28acoustics%29#Binaural_beats) can be produced when sinusoids of slightly differing frequencies are presented to the two ears.
Use the techniques you have learned above to generate a sound of 10-second duration in which the left ear receives a 220Hz pure tone and the right ear receives a 222Hz pure tone.

### Statistics in Python

Using a programming language like Python is a great way to run statistical analyses.
Python has functionality to run many of the standard statistical analyses you will encounter, as shown in the table below, and is also powerful enough to allow you to develop your own custom analyses.

| Test | Python |
| :--- | :--- |
| One-sample $t$ test | `scipy.stats.ttest_1samp` |
| Independent-samples $t$ test | `scipy.stats.ttest_ind` |
| Paired-samples $t$ test | `scipy.stats.ttest_rel` |
| Pearson corrrelation | `scipy.stats.pearsonr` |
| Spearman rank correlation | `scipy.stats.spearmanr` |
| ANOVA | `pingouin.anova` |
| Within-subjects ANOVA | `pingouin.rm_anova` |
| Bayesian methods | `pymc3` |

For me, one of the great advantages of programming is that it makes statistical concepts easier to understand.
A primary reason for this is the ability to *simulate*.

Here, we are going to simulate the behaviour of a simple independent-samples $t$ test.
In particular, we are going to check that the false-positive rate does indeed match the specified $\alpha$ level when the null hypothesis is true.

As per the above table, the Python function for running an independent-samples $t$ test is in `scipy.stats`&mdash;so we start by importing it:

In [ ]:
import scipy.stats

Now we need to define some parameters for our simulated experiments.
Let's assume that we are collecting 20 participants in each of two groups.

In [ ]:
n_per_group = 20

Furthermore, we assume that the values for each participant within a group are drawn from a Normal distribution with a mean of 0 and a standard deviation of 1.
We also assume that the null hypothesis is true and the means of the two group distributions are identical (both 0).

In [ ]:
group_a_mean = 0.0
group_b_mean = 0.0
group_sd = 1.0

Now, we can simulate the running of an experiment by using `np.random.normal` to draw random samples (like we saw previously with `np.random.randint`):

In [ ]:
group_a_data = np.random.normal(loc=group_a_mean, scale=group_sd, size=n_per_group)
group_b_data = np.random.normal(loc=group_b_mean, scale=group_sd, size=n_per_group)

We can take a look at the data we have simulated using the `plt.hist` function to generate a histogram:

In [ ]:
plt.figure();
plt.hist(group_a_data, alpha=0.5, label="Group A");
plt.hist(group_b_data, alpha=0.5, label="Group B");
plt.xlabel("Data value");
plt.ylabel("Frequency");
plt.legend();

Now we want to run an independent-samples $t$ test on our simulated data.
Inspecting the help for `scipy.stats.ttest_ind`, we can see that the function accepts `a` and `b` parameters with the data and gives us back a `statistic` ($t$ value) and a `pvalue`.

In [ ]:
(t, p) = scipy.stats.ttest_ind(a=group_a_data, b=group_b_data)

In [ ]:
print(t, p)

(Note the use of 'unpacking' in the above example. We know that `scipy.stats.ttest_ind` will be giving us back two items, so we explicitly assign those to two different variables.)

Now, we want to run the same 'experiment' lots and lots of times&mdash;a good situation for a `for` loop.

First, let's define how many times:

In [ ]:
n_sims = 10000

We are going to do this two different ways.
The first time, we are going to count the number of times that an 'experiment' is declared statistically significant on the basis of the independent-samples $t$ test giving a $p$ value of $< 0.05$.

We start by defining a variable that will hold how many times we have found a significant result:

In [ ]:
n_significant = 0

Before we write our loop, we need to think about how we will decide whether to increment (add one to) the `n_significant` variable.
Practically, it is straightforward&mdash;we increment `n_significant` if the value of `p` is less than 0.05.

Such 'conditional' statements have a fairly straightforward translation into Python:

In [ ]:
if p < 0.05:
    n_significant += 1

Note the use of a new Python construct here, the `if` statement.

The `if` keyword is followed by a Boolean value (remember those? An expression that evaluates to `True` or `False`) and then a colon.
Any statements that are indented following this colon are only executed if the preceding Boolean value was `True`.
If it was `False`, those statements are skipped.

Note also the use of `+=`; that is shorthand for `n_significant = n_significant + 1`.

OK, now we are ready for our loop!
We loop over a numerical range that has `n_sims` number of items, each time 'running an experiment' and evaluating the `p` value.

In [ ]:
n_significant = 0

for i_sim in range(n_sims):
    
    group_a_data = np.random.normal(loc=group_a_mean, scale=group_sd, size=n_per_group)
    group_b_data = np.random.normal(loc=group_b_mean, scale=group_sd, size=n_per_group)
    
    (t, p) = scipy.stats.ttest_ind(a=group_a_data, b=group_b_data)
    
    if p < 0.05:
        n_significant += 1

It might take a few seconds to run; after all, you are running 10,000 experiments!

Now we can look at the contents of the `n_significant` variable to see on how many of those simulated experiments we declared statistical significance.
Remember that the null hypothesis is true in this scenario&mdash;we made it so when we defined the group mean parameters.

What do you think the value of `n_significant` should be, given our $\alpha$ value of 0.05?

In [ ]:
print(n_significant)

In [ ]:
print(n_significant / n_sims)

Note that it is a simulation, so it won't be exact&mdash;it would become more precise with more simulations.

Now, we are going to do the same thing but this time we will save the `p` values from each 'experiment', so we can see what the distribution of `p` values looks like.

The process is pretty much the same, we just need to first define a variable that will hold the `p` values:

In [ ]:
p_values = np.ones(n_sims)

Then we run our loop, this time saving the `p` value from a given experiment into the relevant index of our `p_values` array:

In [ ]:
for i_sim in range(n_sims):
    
    group_a_data = np.random.normal(loc=group_a_mean, scale=group_sd, size=n_per_group)
    group_b_data = np.random.normal(loc=group_b_mean, scale=group_sd, size=n_per_group)
    
    (t, p) = scipy.stats.ttest_ind(a=group_a_data, b=group_b_data)
    
    p_values[i_sim] = p

Now we can have a look at the distribution of `p` values under the null hypothesis:

In [ ]:
plt.figure();
plt.hist(p_values);
plt.xlabel("$p$ value");
plt.ylabel("Frequency");

*Exercise*: Statistical 'power' can be defined as the probability that the null hypothesis would be rejected when the null hypothesis is false. Adapt the above simulation approach to estimate the statistical power to detect an effect size of 0.5 (i.e., `group_a_mean = 0.0` and `group_b_mean = 0.5`, given `group_sigma = 1.0`) if you have 20 participants per group.